<img src="https://github.com/lid-ufpa/genial/blob/main/assets/genial-logo-banner-dark.png?raw=true" style="width:100%; height:auto;">

# **Aula 3 - Otimização por Colônia de Formigas (ACO)**

## 3.1 Introdução

O algoritmo de Otimização de Colônia de Formigas ou Ant Colony Optimization (ACO) é uma técnica de busca e otimização inspirada no comportamento coletivo das formigas na natureza. Proposto por Marco Dorigo na década de 1990, esse método utiliza princípios de cooperação e auto-organização para encontrar soluções eficientes para problemas complexos, especialmente em contextos de otimização combinatória.

Imagine uma colônia de formigas em busca de alimento. No início, nenhuma delas sabe exatamente onde a fonte de comida está localizada. Assim, as primeiras formigas deixam o ninho e começam a se deslocar de maneira quase aleatória pelo espaço. Durante o percurso, elas liberam pequenas quantidades de feromônios, substâncias químicas que funcionam como sinais de orientação para outras formigas.

Com o tempo, algumas formigas acabam encontrando uma fonte de alimento. Ao retornar ao ninho, elas reforçam o rastro de feromônios deixado no caminho de ida. Esse processo cria uma trilha que indica às companheiras que existe algo promissor naquela direção.

Agora, imagine que existem dois caminhos possíveis ligando o formigueiro à mesma fonte de alimento: um curto e outro mais longo. No início, parte das formigas escolhe aleatoriamente o caminho mais curto, enquanto outras seguem pelo mais longo. Porém, as formigas que percorrem o trajeto curto conseguem fazer mais viagens de ida e volta em menos tempo, reforçando o rastro de feromônios de forma mais intensa. Já no caminho mais longo, a reposição de feromônios ocorre mais lentamente.

Como os feromônios evaporam naturalmente ao longo do tempo, os rastros fracos tendem a desaparecer, enquanto os rastros mais fortes se tornam cada vez mais atrativos para novas formigas. Esse mecanismo faz com que quase toda a colônia passe a seguir o trajeto mais eficiente.

<p align="center">
  <img src="https://github.com/lid-ufpa/genial/blob/main/aulas/utils/imagens/aco.png?raw=true" width="400">
</p>

## 3.2 Estrutura

- **Representação:** grafo, onde os vértices representam estados e as arestas representam opções de transição entre eles.
- **Formigas:** agentes independentes que constroem soluções, escolhendo o próximo vértice de forma probabilística.
- **Feromônios:** valores armazenados nas arestas que refletem a atratividade delas.
- **Heurística:** informação adicional que orienta a busca.
- **Regra de Transição:** fórmula que combina o nível de feromônio e a heurística para definir a probabilidade de escolha do próximo vértice.
- **Função Objetivo:** avalia a qualidade de cada solução.

## 3.3 Etapas

1. **Inicialização:** os parâmetros do algoritmo e os valores iniciais de feromônio são definidos.
2. **Construção das Soluções:** cada formiga parte de um estado inicial e, aplicando a regra de transição, seleciona sucessivamente vértices até formar uma solução.
3. **Avaliação das Soluções:** todas as soluções geradas são avaliadas pela função objetivo e a melhor solução é armazenada.
4. **Atualização dos Feromônios:** os valores de feromônio em todas as arestas são reduzidos (evaporação), então os valores de feromônio nas arestas usadas são aumentados (depósito).
5. **Iteração:** o ciclo de construção–avaliação–atualização se repete até que seja atingido um critério de parada.

## 3.4 Definição Formal

Seja $G = (V, E)$ um grafo em que cada vértice $v \in V$ representa um estado, e cada aresta $(i,j) \in E$ representa uma transição entre estados, associada a um feromônio $\tau_{ij}$. Considere também uma heurística $\eta_{ij}$ e uma função objetivo $f : \mathcal{S} \to \mathbb{R}$, onde $\mathcal{S}$ é o conjunto de soluções possíveis, tal que $f(s)$ fornece o custo da solução $s$. 

O problema de otimização pode ser formulado como:

$$
s^* = \arg\min_{s \in \mathcal{S}} f(s),
$$

ou, de modo equivalente, em termos de maximização:

$$
s^* = \arg\min_{s \in \mathcal{S}} -f(s),
$$

onde $s^*$ é a melhor solução encontrada de acordo com a função objetivo $f$.

---

O algoritmo é iterativo. Em cada iteração $t = 1, 2, \dots, T$:  
1. Cada formiga constrói uma solução $s_k^t$ ao percorrer o grafo.  
2. Cada solução é avaliada pela função objetivo $f(s_k^t)$.  
3. Os níveis de feromônio $\tau_{ij}$ são atualizados (evaporação + depósito).  
4. A melhor solução global $s^*$ é atualizada: 
   $$
   s^* \leftarrow \arg\min_{s \in \{s^*, s_k^t\}} f(s).
   $$

Esse ciclo é repetido até que se atinja o critério de parada (número máximo de iterações, tempo limite ou ausência de melhoria).

---

A regra de transição que determina a escolha do próximo estado $j$ pela formiga $k$, estando em $i$, é:

$$
P^k_{ij} =
\begin{cases}
\dfrac{\tau_{ij}^\alpha \, \eta_{ij}^\beta}{\sum\limits_{l \in N_i^k} \tau_{il}^\alpha \, \eta_{il}^\beta}, & \text{se } j \in N_i^k, \\[10pt]
0, & \text{caso contrário},
\end{cases}
$$

onde $N_i^k$ é o conjunto de estados que a formiga $k$ ainda pode acessar a partir de $i$, 
e $\alpha, \beta > 0$ são pesos que determinam a influência do feromônio e da heurística.

---

A evaporação dos feromônios é dada por: $$ \tau_{ij} \leftarrow (1 - \rho)\,\tau_{ij}, $$ onde $\rho \in (0,1]$ é a taxa de evaporação. Já o depósito é dado por: $$ \tau_{ij} \leftarrow \tau_{ij} + \sum_{k=1}^m \Delta \tau_{ij}^k, $$ com: $$ \Delta\tau_{ij}^k = \begin{cases} \dfrac{Q}{L_k}, & \text{se a formiga $k$ usou a aresta $(i,j)$ na sua solução}, \\[10pt] 0, & \text{caso contrário}, \end{cases} $$ em que $m$ é o número total de formigas, $Q > 0$ é uma constante, e $L_k = f(s_k)$ é o custo da solução $s_k$ construída pela formiga $k$ segundo a função objetivo $f$.

## 3.5 Exemplo

### 3.5.1 Problema do Caixeiro Viajante (TSP)

O Problema do Caixeiro Viajante consiste em encontrar o menor caminho que percorra todas as cidades de um conjunto, passando apenas uma vez por cada cidade e retornando à cidade de origem. Esse problema é considerado NP-difícil, o que significa que algoritmos exatos tornam-se inviáveis quando o número de cidades cresce. Por isso, o TSP é um dos problemas clássicos onde metaheurísticas são aplicadas.

### 3.5.2 Representação do Problema

O **TSP** é modelado como um grafo completo, em que:

- **Vértices:** representam as cidades.  
- **Arestas:** representam os caminhos possíveis entre as cidades.  
- **Custo:** representam as distâncias euclidianas entre as cidades.

Essa estrutura pode ser representada por uma matriz de custos $C$, onde cada elemento $C_{ij}$ indica o custo de ir da cidade $i$ para a cidade $j$:

$$
C =
\begin{bmatrix}
0 & c_{12} & c_{13} & \dots & c_{1n} \\
c_{21} & 0 & c_{23} & \dots & c_{2n} \\
\vdots & \vdots & \ddots & \vdots & \vdots \\
c_{n1} & c_{n2} & \dots & 0
\end{bmatrix}
$$

- A diagonal principal contém zeros, pois o custo de ir de uma cidade para ela mesma é nulo.  
- A matriz pode ser simétrica (distância de $i$ para $j$ é igual à de $j$ para $i$) ou assimétrica (quando há diferença, como em custos de tráfego ou logística).  

---

Uma solução para o TSP é uma permutação dos vértices (cidades), que define a ordem de visitação.

Por exemplo, considere 4 cidades e a matriz de custos:

$$
C =
\begin{bmatrix}
0 & 10 & 15 & 20 \\
10 & 0 & 35 & 25 \\
15 & 35 & 0 & 30 \\
20 & 25 & 30 & 0
\end{bmatrix}
$$

Uma solução possível é a rota:

$$
[0, 2, 3, 1, 0]
$$

O custo total dessa solução é calculado somando os valores correspondentes da matriz:

$$
C_{0,2} + C_{2,3} + C_{3,1} + C_{1,0}
= 15 + 30 + 25 + 10 = 80
$$

### 3.5.3 Código em Python

A seguir, um exemplo de implementação do ACO aplicado ao TSP usando **programação orientada a objetos**.

In [1]:
import random

from IPython.display import HTML

from utils.funcoes_auxiliares.animar_aco import animar_aco

In [ ]:
class TSPACO:
    """Implementação do algoritmo de Otimização por Colônia de Formigas (ACO) para o Problema do Caixeiro Viajante (TSP)."""

    def __init__(self, custos, n_formigas, alfa, beta, n_iteracoes, taxa_evaporacao):
        self.custos = custos

        # Matriz de feromônio inicial (valores iguais)
        n = len(custos)
        self.feromonios = [[1.0 / n for _ in range(n)] for _ in range(n)]

        # Lista de vértices (índices das cidades)
        self.vertices = list(range(n))

        # Parâmetros do algoritmo
        self.n_formigas = n_formigas
        self.n_iteracoes = n_iteracoes
        self.alfa = alfa
        self.beta = beta
        self.taxa_evaporacao = taxa_evaporacao

        # Melhor solução encontrada até o momento
        self.melhor_solucao = []
        self.melhor_custo = float("inf")

        # Histórico de iterações (para visualização)
        self.historico = []

    # --------------------------------------------------------------
    # Construção de soluções
    # --------------------------------------------------------------
    def _construir_solucao(self, vertice_inicial):
        """Constrói uma solução completa a partir de uma formiga."""
        solucao = []
        visitados = {vertice_inicial}
        vertice_atual = vertice_inicial

        # Visita todos os vértices (menos o inicial, que já foi)
        for _ in range(len(self.custos) - 1):
            # Vértices ainda não visitados
            candidatos = [v for v in self.vertices if v not in visitados]

            if not candidatos:
                continue

            # Calcula as probabilidades de transição para cada candidato
            probabilidades = self._probabilidades_transicao(vertice_atual, candidatos)

            # Sorteia o próximo vértice de acordo com as probabilidades
            proximo_vertice = random.choices(candidatos, weights=probabilidades, k=1)[0]

            # Atualiza solução e conjuntos
            solucao.append((vertice_atual, proximo_vertice))
            visitados.add(proximo_vertice)
            vertice_atual = proximo_vertice

        # Fecha o ciclo (volta ao vértice inicial)
        solucao.append((vertice_atual, vertice_inicial))

        # Calcula o custo da solução
        custo_total = sum(self.custos[i][j] for i, j in solucao)

        return solucao, custo_total

    def _construir_solucoes(self, vertice_inicial):
        """Constrói soluções para todas as formigas em uma iteração."""
        solucoes = []

        for _ in range(self.n_formigas):
            solucao, custo = self._construir_solucao(vertice_inicial)
            solucoes.append((solucao, custo))

            # Atualiza o melhor global
            self._atualizar_melhor_global(solucao, custo)

        return solucoes

    # --------------------------------------------------------------
    # Probabilidades de transição
    # --------------------------------------------------------------
    def _probabilidades_transicao(self, vertice_atual, candidatos):
        """Calcula as probabilidades de transição para os vértices candidatos."""
        numeradores = []

        for j in candidatos:
            # Influência do feromônio (τ)
            tau = self.feromonios[vertice_atual][j] ** self.alfa

            # Influência da heurística (η = 1/distância)
            eta = (
                (1.0 / self.custos[vertice_atual][j]) ** self.beta
                if self.custos[vertice_atual][j] > 0
                else 0
            )

            numeradores.append(tau * eta)

        denominador = sum(numeradores)

        # Se não houver diferença, assume probabilidades iguais
        if denominador == 0:
            return [1.0 / len(candidatos)] * len(candidatos)

        return [num / denominador for num in numeradores]

    # --------------------------------------------------------------
    # Atualização dos feromônios
    # --------------------------------------------------------------
    def _atualizar_feromonios(self, solucoes):
        """Atualiza os feromônios após todas as formigas construírem suas soluções."""
        n = len(self.custos)
        delta_feromonios = [[0.0 for _ in range(n)] for _ in range(n)]

        # Cada formiga deposita feromônio proporcional ao inverso do custo
        for solucao, custo in solucoes:
            for i, j in solucao:
                delta_feromonios[i][j] += 1.0 / custo

        # Aplica evaporação e deposição
        for i in range(n):
            for j in range(n):
                self.feromonios[i][j] = (1 - self.taxa_evaporacao) * self.feromonios[i][j]
                self.feromonios[i][j] += delta_feromonios[i][j]

    # --------------------------------------------------------------
    # Atualização da melhor solução global
    # --------------------------------------------------------------
    def _atualizar_melhor_global(self, solucao, custo):
        """Atualiza a melhor solução global encontrada até agora."""
        if custo < self.melhor_custo:
            self.melhor_custo = custo
            self.melhor_solucao = solucao

    # --------------------------------------------------------------
    # Execução principal
    # --------------------------------------------------------------
    def otimizar(self, vertice_inicial):
        """Executa o algoritmo ACO para otimizar o TSP. Retorna a melhor rota e seu custo."""
        self.historico = []

        for i in range(self.n_iteracoes):
            # Constrói soluções para todas as formigas
            solucoes = self._construir_solucoes(vertice_inicial)

            # Atualiza feromônios com base nas soluções encontradas
            self._atualizar_feromonios(solucoes)

            # Salva informações da iteração no histórico
            entrada_historico = {
                "iteracao": i,
                "melhor_solucao": self.melhor_solucao[:],
                "melhor_custo": self.melhor_custo,
                "feromonios": [linha[:] for linha in self.feromonios],
            }
            self.historico.append(entrada_historico)

        # Constrói a lista final de vértices visitados
        melhor_caminho_vertices = [i for i, j in self.melhor_solucao] + [vertice_inicial]

        return melhor_caminho_vertices, self.melhor_custo


Define os parâmetros principais para o algoritmo.

In [3]:
N_CIDADES = 20
N_FORMIGAS = 20
N_ITERACOES = 100
ALFA = 1.0
BETA = 3.0
TAXA_EVAPORACAO = 0.7
VERTICE_INICIAL = 0

Define a `seed` do gerador de números aleatórios para garantir reprodutibilidade dos resultados.

In [4]:
random.seed(42)

Cria coordenadas aleatórias para as cidades e calcula a matriz de distâncias entre todas as cidades usando a distância euclidiana.

In [5]:
coordenadas_cidades = [(random.uniform(0, 100), random.uniform(0, 100)) for _ in range(N_CIDADES)]
distancias = [[0.0 for _ in range(N_CIDADES)] for _ in range(N_CIDADES)]

for i in range(N_CIDADES):
    for j in range(N_CIDADES):
        if i != j:
            x = (coordenadas_cidades[i][0] - coordenadas_cidades[j][0]) ** 2
            y = (coordenadas_cidades[i][1] - coordenadas_cidades[j][1]) ** 2
            distancias[i][j] = (x + y) ** (1/2)

Inicializa uma instância da classe `TSPACO` com a matriz de distâncias, o número de formigas, alfa, beta, número de iterações e a taxa de evaporação definida.

In [6]:
aco = TSPACO(
    custos=distancias,
    n_formigas=N_FORMIGAS,
    alfa=ALFA,
    beta=BETA,
    n_iteracoes=N_ITERACOES,
    taxa_evaporacao=TAXA_EVAPORACAO,
)

Executa o algoritmo com o vértice inicial e exibe a melhor rota encontrada e o seu custo.

In [7]:
melhor_rota, melhor_custo = aco.otimizar(VERTICE_INICIAL)

print("Melhor rota encontrada:", melhor_rota)
print("Custo da melhor rota encontrada:", melhor_custo)

Melhor rota encontrada: [0, 4, 11, 1, 6, 13, 5, 8, 17, 7, 19, 14, 18, 10, 15, 2, 16, 12, 3, 9, 0]
Custo da melhor rota encontrada: 391.4124656744334


Gera e exibe uma animação mostrando a variação da melhor rota ao longo das iterações.

In [8]:
ani = animar_aco(aco, coordenadas_cidades)
HTML(ani.to_jshtml())

## 3.6 Vantagens e Desvantagens

### 3.6.1 Vantagens

- **Paralelização Natural:** como as formigas funcionam como agentes independentes, o algoritmo pode ser facilmente paralelizado em múltiplos processadores ou em sistemas distribuídos.

- **Exploração vs. Intesificação:** o mecanismo de reforço do feromônio (exploração) e da evaporação (diversificação) cria um equilíbrio natural entre intensificação (explorar soluções boas já conhecidas) e diversificação (buscar novas soluções).

- **Flexibilidade de Aplicação:** pode ser adaptado para uma variedade de problemas (logística, telecomunicações, engenharia, bioinformática etc).

### 3.6.2 Desvantagens

- **Risco de Convergência Prematura:** se algumas soluções são reforçadas cedo demais, o algoritmo pode ficar preso em ótimos locais, pois o excesso de feromônio num caminho pode desestimular a exploração de alternativas.

- **Alto Custo Computacional:** a manutenção da matriz de feromônio e a simulação de muitas formigas podem ser computacionalmente custosas, especialmente em problemas com espaço de busca muito grande.

- **Sensibilidade a Parâmetros:** o desempenho depende fortemente de parâmetros como: taxa de evaporação do feromônio, peso entre feromônio e heurística, número de formigas. Pequenas mudanças podem alterar muito a qualidade da solução.